# Edge Modes for the Haldane Honeycomb

To calculate the edge modes, instead of solving a bulk, 2D system, we solve a 1 dimensional system with a large unit cell.
![Edges](edges.svg)

\begin{equation}
  \mathcal{H}=
  \sum_{\text{unit}}\left(
  \sum_{i=1}^{\text{rows}}
  \frac{1}{2} \left( S_{a_i,r} \cdot S_{b_i,r-1}
  + S_{b_i,r} \cdot S_{a_i,r+1} \right)
 + S_{a_i,r} \cdot S_{b_i,r}
  \right)+
  \left( \sum_{j=1}^{\text{rows}-1}
  S_{b_j,r} \cdot S_{a_j,r}\right)
\end{equation}
\begin{equation}
S_i \cdot S_j \rightarrow
\frac{1}{2} \left(
\frac{1}{2} - a_i^{\dagger} a_i - b_j^{\dagger} b_j + a_i^{\dagger} b_j + a_i b_j^{\dagger}
\right)
\end{equation}

\begin{equation}
  \mathcal{H} = \frac{11 N}{4} +
  \begin{bmatrix}
  a_1^{\dagger} \\ b_1^{\dagger} \\
  a_2^{\dagger} \\ b_2^{\dagger} \\
   a_3^{\dagger} \\ b_3^{\dagger} \\
    a_4^{\dagger} \\ b_4^{\dagger}
  \end{bmatrix}^{T}
\begin{bmatrix}
-1  &  w(k)  &0&0 &0&0 &0&0\\ %a_1
w^{*}(k) & -\frac{3}{2}  & \frac{1}{2} &0 &0&0 &0&0\\ %b_1
0&  \frac{1}{2} & -\frac{3}{2}  & w(k) &0&0 &0&0\\ %a_2
0&0& w^{*}(k)&-\frac{3}{2} & \frac{1}{2}&0 &0&0\\ %b_2
0&0& 0& \frac{1}{2}& -\frac{3}{2}&w(k) &0&0\\ %a_3
0&0& 0&0& w^{*}(k)&-\frac{3}{2} &\frac{1}{2}&0\\ %b_3
0&0& 0&0& 0& \frac{1}{2} &-\frac{3}{2}&w(k)\\ %a_4
0&0& 0&0& 0&0 &w^{*}(k)&-1\\%b_4
\end{bmatrix}
\begin{bmatrix}
a_1\\ b_1\\
a_2\\ b_2\\
 a_3 \\ b_3 \\
  a_4 \\ b_4
\end{bmatrix}
\end{equation}
\begin{equation}
  w(k) =\frac{1}{2} \left( 1 + e^{i \Delta k} \right)
\end{equation}


## Initialization
* Packages
* Momentum coordinates
* Labels

In [1]:
using Plots
plotlyjs()

INFO: Loading HttpServer methods...


Plots.PlotlyJSBackend()

In [2]:
ka=linspace(-π,π,2*314)
l=length(ka)
dks=ka[2]-ka[1]

0.010021029198053366

In [3]:
labels=["-2π","-3π/2","-π","-π/2","0","π/2","π","3π/2","2π"]
ticks=[-2π,-3π/2,-π,-π/2,0,π/2,π,3π/2,2π];

## Getting the site positions

In [4]:
Nx=20
Ny=20
Nz=1

1

In [5]:
d=2;
Ncell=2;
unit=[[0 0 0]
    [cos(π/6) sin(π/6) 0]];
a=[sqrt(3),0,0];
b=[sqrt(3)/2,3/2,0];
c=[0,0,1];

In [6]:
# Another cell to just evaluate
# Here we set up some numbers and matrices for our computation
N=Nx*Ny*Nz*Ncell;    #The total number of sites
aM=transpose(repeat(a,outer=[1,Ncell]));
bM=transpose(repeat(b,outer=[1,Ncell*Nx])); #these allow us to copy an entire row or layer at once
cM=transpose(repeat(c,outer=[1,Ncell*Nx*Ny]));

X=Array{Float64}(N,3);  #where we store the positions
"Cell finished"

"Cell finished"

In [7]:
# Another cell to just evaluate
# Here we are actually calculating the positions for every site
for i in 1:Nx    #for the first row
    X[Ncell*i-Ncell+1:Ncell*i,:]=unit+(i-1)*aM;
end

for j in 2:Ny    #copying the first row into the first layer
    X[Ncell*Nx*(j-1)+(1:Ncell*Nx),:]=X[1:Ncell*Nx,:]+(j-1)*bM;
end

for j in 2:Nz    #copying the first layer into the entire cube
    X[Ncell*Ny*Nx*(j-1)+(1:Ncell*Nx*Ny),:]=X[1:Ncell*Nx*Ny,:]+(j-1)*cM;
end
"Cell finished"

"Cell finished"

In [8]:
scatter(X[:,1],X[:,2])

## Constructing Hamiltonian

In [9]:
f(k::Float64)=1/2*(1+exp(im*k))

f (generic function with 1 method)

In [10]:
function mat(k::Float64,n::Int=4)
    matr=-3./2.*eye(Complex{Float64},n*2)
    
    matr[1,1]=-1.
    matr[n*2,n*2]=-1.
    
    for ii in 1:n
        matr[2*ii-1,2*ii]=f(k)
        matr[2*ii,2*ii-1]=conj(f(k))
    end
    for ii in 1:n-1
        matr[2*ii,2*ii+1]=1/2
        matr[2*ii+1,2*ii]=1/2
    end
    return matr
end

mat (generic function with 2 methods)

In [11]:
n=12

E=Array{Float64}(l,2*n)

v=Array{Array{Complex{Float64}}}(l,2*n)
for ii in 1:l
    fact=eigfact(mat(ka[ii],n))
        
    for jj in 1:2*n
        E[ii,jj]=fact[:values][jj]
        v[ii,jj]=fact[:vectors][:,jj]
    end
end

So the second value indicates which band energy we are talking about, the third index is what site we are talking about, the first index is the momentum

In [12]:
vmod=Array{Complex{Float64}}(l,2*n,2*n)
for ii in 1:l
    for jj in 1:2*n
        for kk in 1:2*n
            vmod[ii,jj,kk]=v[ii,jj][kk]      
        end
    end
end

In [13]:
plot(ka,E[:,:])
plot!(xlabel="Momentum",xticks=(ticks,labels)
,ylabel="Energy",title="Energy",title="Energy bands for Strip, no DM, n=$n"
,legend=false,
background_color_inside=RGBA(0,0,0,0),
background_color_outside=RGBA(0,0,0,0))

In [14]:
band=E[:,n]-minimum(E[:,n])
band=band-maximum(band)/2
plot(ka,band,xticks=(ticks,labels))
scatter!(ka[abs.(band).<2.5e-3],band[abs.(band).<2.5e-3])

In [15]:
collect(1:length(band))[abs.(band).<2.5e-3]

4-element Array{Int64,1}:
 105
 106
 523
 524

In [16]:
cspace = :inferno

ii=525

t=norm.(vmod[ii,n,:]).^2
t1=t[1:2:end]
t1=repmat(t1,1,Nx)
t1=transpose(t1)[1:end]
t1=10.*t1./maximum(t1)

t2=t[2:2:end]
t2=repmat(t2,1,Nx)
t2=transpose(t2)[1:end]
t2=10.*t2./maximum(t2)

ksliced=ka[ii]
phase1=1/(2π)*mod.(ksliced.*X[1:2:end,1],2π);
phasecolor1=[cgrad(cspace)[ii] for ii in phase1]
phase2=1/(2π)*mod.(ksliced.*X[2:2:end,1],2π);
phasecolor2=[cgrad(cspace)[ii] for ii in phase2]

scatter(X[1:2:end,1],X[1:2:end,2],markersize=t1,markercolor=phasecolor1,
    markerstrokewidth=0)
scatter!(X[2:2:end,1],X[2:2:end,2],markersize=t2,markercolor=phasecolor2,
    markerstrokewidth=0)

plot!(Shape([0,X[Nx*2,1],X[end,1],X[end-Nx*2+1,1]],
[0,0,X[end,2],X[end-Nx*2+1,2]]),opacity=.1)

plot!(legend=false, xlabel="X position", ylabel="Y position"
,title="Open Boundries on Strip, k=$(round(ksliced,2)) ε=1/2 Emax",
background_color_inside=RGBA(0,0,0,0),
background_color_outside=RGBA(0,0,0,0))
plot!(legend=false)

In [17]:
plot(norm.(vmod[:,n+1,1]))
plot!(norm.(vmod[:,n+1,2]))
plot!(norm.(vmod[:,n+1,3]))
plot!(norm.(vmod[:,n+1,4]))
plot!(norm.(vmod[:,n+1,5]))

## DM Hamiltonian

In [18]:
D=0.1
f(k::Float64)=1/2*(1+exp(im*k))
g(k::Float64) = - D * im/2 *(exp(-im*k) - exp(im*k))
h(k::Float64) = -D*im/2*(1+exp(im*k))

h (generic function with 1 method)

In [19]:
function matDM(k::Float64,n::Int=4)
    matr=(-3./2.)*eye(Complex{Float64},n*2)
    
    matr[1,1]=-1
    matr[n*2,n*2]=-1
    
    for ii in 1:2*n
        matr[ii,ii]+=(-1)^(ii+1)*g(k)
    end
    
    for ii in 1:n
        matr[2*ii-1,2*ii]=f(k)
        matr[2*ii,2*ii-1]=conj(f(k))
    end
    
    for ii in 1:(n-1)
        matr[2*ii-1,2*ii+1]=h(k)
        #println("a",2*ii-1,"\t",2*ii+1)
        matr[2*ii+1,2*ii-1]=conj(h(k))
    end
    
    for ii in 1:n-1
        matr[2*ii,2*ii+1]=1/2
        matr[2*ii+1,2*ii]=1/2
        
        matr[2*ii,2*ii+2]=-h(k)
        #println("b",2*ii,"\t",2*ii+2)
        matr[2*ii+2,2*ii]=-conj(h(k))
    end
    
    return matr
end

matDM (generic function with 2 methods)

In [20]:
n=Ny

EDM=Array{Float64}(l,2*n)

vDM=Array{Array{Complex{Float64}}}(l,2*n)
for ii in 1:l
    fact=eigfact(matDM(ka[ii],n))
        
    for jj in 1:2*n
        EDM[ii,jj]=fact[:values][jj]
        vDM[ii,jj]=fact[:vectors][:,jj]
    end
end

vmodDM=Array{Complex{Float64}}(l,2*n,2*n)
for ii in 1:l
    for jj in 1:2*n
        for kk in 1:2*n
            vmodDM[ii,jj,kk]=vDM[ii,jj][kk]      
        end
    end
end

In [21]:
plot(ka,E)
plot!(xlabel="Momentum",xticks=(ticks,labels)
,ylabel="Energy",title="Energy",title="Energy bands for Strip, with DM,n=$n"
,legend=false,
background_color_inside=RGBA(0,0,0,0),
background_color_outside=RGBA(0,0,0,0))

In [22]:
band=EDM[:,n]-minimum(EDM[:,n])
band=band-maximum(band)/2
plot(ka,band,xticks=(ticks,labels))
scatter!(ka[abs.(band).<2.5e-3],band[abs.(band).<2.5e-3])

In [23]:
collect(1:length(band))[abs.(band).<2.5e-3]

2-element Array{Int64,1}:
 104
 525

In [24]:
plot(norm.(vmodDM[104,n,:]).^2)
plot!(norm.(vmodDM[525,n,:]).^2)

In [25]:
cspace = :pu_or

:pu_or

In [26]:
ii=525

t=norm.(vmodDM[ii,n,:]).^2
t1=t[1:2:end]
t1=repmat(t1,1,Nx)
t1=transpose(t1)[1:end]
t1=10.*t1./maximum(t1)

t2=t[2:2:end]
t2=repmat(t2,1,Nx)
t2=transpose(t2)[1:end]
t2=10.*t2./maximum(t2)

ksliced=ka[ii]
phase1=1/(2π)*mod.(ksliced.*X[1:2:end,1],2π);
phasecolor1=[cgrad(cspace)[ii] for ii in phase1]
phase2=1/(2π)*mod.(ksliced.*X[2:2:end,1],2π);
phasecolor2=[cgrad(cspace)[ii] for ii in phase2]

scatter(X[1:2:end,1],X[1:2:end,2],markersize=t1,markercolor=phasecolor1,
    markerstrokewidth=0)
scatter!(X[2:2:end,1],X[2:2:end,2],markersize=t2,markercolor=phasecolor2,
    markerstrokewidth=0)

plot!(Shape([0,X[Nx*2,1],X[end,1],X[end-Nx*2+1,1]],
[0,0,X[end,2],X[end-Nx*2+1,2]]),opacity=.1)

plot!(legend=false, xlabel="X position", ylabel="Y position"
,title="Open Boundries on Strip, k=$(round(ksliced,2)) ε=1/2 Emax",
background_color_inside=RGBA(0,0,0,0),
background_color_outside=RGBA(0,0,0,0))
plot!(legend=false)

In [27]:
ii=104

t=norm.(vmodDM[ii,n,:]).^2
t1=t[1:2:end]
t1=repmat(t1,1,Nx)
t1=transpose(t1)[1:end]
t1=10.*t1./maximum(t1)

t2=t[2:2:end]
t2=repmat(t2,1,Nx)
t2=transpose(t2)[1:end]
t2=10.*t2./maximum(t2)

ksliced=ka[ii]
dist_Nx=repmat(floor.(collect(1:Nx)),1,Ny);
phase=round.(Int,30/(2π)*mod.(ksliced*dist_Nx[1:end],2π));
phasecolor=[cgrad(cspace)[ii] for ii in phase]

scatter(X[1:2:end,1],X[1:2:end,2],markersize=t1,markercolor=phasecolor1,
    markerstrokewidth=0)
scatter!(X[2:2:end,1],X[2:2:end,2],markersize=t2,markercolor=phasecolor2,
    markerstrokewidth=0)

plot!(Shape([0,X[Nx*2,1],X[end,1],X[end-Nx*2+1,1]],
[0,0,X[end,2],X[end-Nx*2+1,2]]),opacity=.1)

plot!(legend=false, xlabel="X position", ylabel="Y position"
,title="Open Boundries on Strip, k=$(round(ksliced,2)) ε=1/2 Emax",
background_color_inside=RGBA(0,0,0,0),
background_color_outside=RGBA(0,0,0,0))
plot!(legend=false)

In [28]:
ii=104

msize2=norm.(vmod[104,n,:]).^2;
msize2=30*msize2./maximum(msize2);
msize3=repmat(msize2,1,2*Nx)
msize3=transpose(msize3)
msize3=msize3[1:end];

ksliced=ka[ii]
dist_Nx=repmat(floor.(collect(1:.5:(Nx+.5))),1,2*Ny);
phase=mod.(ksliced*dist_Nx[1:end],2π);